<a href="https://colab.research.google.com/github/pen1064/Toronto_House_Market/blob/main/Prepare_Neighborhood_Income.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
%%time 

# Important library for many geopython libraries
!apt install gdal-bin python-gdal python3-gdal 
# Install rtree - Geopandas requirment
!apt install python3-rtree 
# Install Geopandas
!pip install git+git://github.com/geopandas/geopandas.git
# Install descartes - Geopandas requirment
!pip install descartes 
# Install Folium for Geographic data visualization
!pip install folium
# Install plotlyExpress
!pip install plotly_express

Reading package lists... Done
Building dependency tree       
Reading state information... Done
gdal-bin is already the newest version (2.2.3+dfsg-2).
python-gdal is already the newest version (2.2.3+dfsg-2).
The following packages were automatically installed and are no longer required:
  cuda-command-line-tools-10-0 cuda-command-line-tools-10-1
  cuda-command-line-tools-11-0 cuda-compiler-10-0 cuda-compiler-10-1
  cuda-compiler-11-0 cuda-cuobjdump-10-0 cuda-cuobjdump-10-1
  cuda-cuobjdump-11-0 cuda-cupti-10-0 cuda-cupti-10-1 cuda-cupti-11-0
  cuda-cupti-dev-11-0 cuda-documentation-10-0 cuda-documentation-10-1
  cuda-documentation-11-0 cuda-documentation-11-1 cuda-gdb-10-0 cuda-gdb-10-1
  cuda-gdb-11-0 cuda-gpu-library-advisor-10-0 cuda-gpu-library-advisor-10-1
  cuda-libraries-10-0 cuda-libraries-10-1 cuda-libraries-11-0
  cuda-memcheck-10-0 cuda-memcheck-10-1 cuda-memcheck-11-0 cuda-nsight-10-0
  cuda-nsight-10-1 cuda-nsight-11-0 cuda-nsight-11-1 cuda-nsight-compute-10-0
  cuda-nsig

In [7]:
import pandas as pd
import numpy as np
import geopandas as gpd
from shapely.geometry import Point
import matplotlib
import matplotlib.pyplot as plt 
import folium
import plotly_express as px
import os


In [31]:
filename = os.path.join(os.getcwd(),"Neighbourhoods.shp")
gdf = gpd.read_file("Neighbourhoods.shp")

In [32]:
gdf.head(3)

FIELD_1  ...                                           geometry
0      141  ...  POLYGON ((309967.120 4837586.769, 310047.783 4...
1      142  ...  POLYGON ((311976.621 4840247.041, 312084.257 4...
2      143  ...  POLYGON ((313572.832 4837693.591, 313555.868 4...

[3 rows x 16 columns]

In [36]:
gdf_columns = pd.read_csv('Neighbourhoods_fields.csv')
gdf.columns = gdf_columns.name.values
gdf['geometry'] = gdf['geometry'].to_crs({'init': 'EPSG:4269'})

gdf.head(3)

/usr/local/lib/python3.7/dist-packages/pyproj/crs/crs.py:131: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  in_crs_string = _prepare_from_proj_string(in_crs_string)


_id  ...                                           geometry
0  141  ...  POLYGON ((-79.43592 43.68015, -79.43492 43.680...
1  142  ...  POLYGON ((-79.41096 43.70408, -79.40962 43.704...
2  143  ...  POLYGON ((-79.39119 43.68108, -79.39141 43.680...

[3 rows x 16 columns]

In [38]:
census_data = pd.read_csv("neighbourhood-profiles-2016-csv.csv")
census_data.head(3)

_id  ...      Yorkdale-Glen Park
0    1  ...                      31
1    2  ...  Emerging Neighbourhood
2    3  ...                  14,804

[3 rows x 146 columns]

In [39]:
income_data = census_data[(census_data.Characteristic == "Neighbourhood Number")|(census_data.Characteristic == "Total income: Average amount ($)")]
income_data=income_data.T.reset_index()
income_data.columns = ['property','neighborhood_id', 'Avg_Income']
income_data.head(10)

property  ...                        Avg_Income
0                           _id  ...                              2273
1                      Category  ...                            Income
2                         Topic  ...                    Income sources
3                   Data Source  ...     Catalogue no. 98-400-X2016122
4                Characteristic  ...  Total income: Average amount ($)
5               City of Toronto  ...                            52,268
6               Agincourt North  ...                            30,414
7  Agincourt South-Malvern West  ...                            31,825
8                     Alderwood  ...                            47,709
9                         Annex  ...                           112,766

[10 rows x 3 columns]

In [40]:
income_data=income_data.iloc[6:,:]
income_data['Avg_Income'] = income_data['Avg_Income'].apply(lambda z: z.replace(',','')).astype('int64')
income_data['neighborhood_id'] = income_data['neighborhood_id'].astype('int64')
income_data.head(3)

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  This is separate from the ipykernel package so we can avoid doing imports until


property  neighborhood_id  Avg_Income
6               Agincourt North              129       30414
7  Agincourt South-Malvern West              128       31825
8                     Alderwood               20       47709

In [47]:
income_gdf = gdf.merge(income_data, left_on=['AREA_SHORT_CODE'], right_on=['neighborhood_id'])
income_gdf.drop("property", inplace=True, axis= 1)
income_gdf.head(10)


_id   AREA_ID  ...  neighborhood_id  Avg_Income
0  141  25886861  ...               94       54460
1  142  25886820  ...              100       89330
2  143  25886834  ...               97      114174
3  144  25886593  ...               27       29958
4  145  25886688  ...               31       38527
5  146  25886404  ...              114       76629
6  147  25886627  ...               38       72371
7  148  25886808  ...              105      111730
8  149  25886812  ...              103      169203
9  150  25886328  ...               56      125564

[10 rows x 18 columns]

In [48]:
income_gdf.to_excel("income_neighborhood.xlsx")

In [69]:
initialize_map = folium.Map(location = [ 43.6532, -79.3832], zoom_start = 12)
initialize_map

In [70]:
add_choropleth = folium.Choropleth(geo_data= income_gdf,  data=income_gdf,
 name='choropleth',
 columns=['AREA_NAME', 'Avg_Income'], ##the columns containing the data
 key_on='feature.properties.AREA_NAME',
 fill_color='YlOrRd', ##color style for the choropleth
 bins = 9,
 fill_opacity=1,
 line_opacity=1,
).add_to(initialize_map)
initialize_map

In [74]:
for i in range(len(income_gdf)):
  name = gdf.loc[i, "AREA_NAME"]
  print(name)
  folium.Marker([income_gdf.loc[i, "LONGITUDE"], income_gdf.loc[i,"LATITUDE"]], icon=folium.DivIcon(html = f"""<div style = "font-family: fantasy
                    ; color: black;=> {"{}".format(name) }</div>  """)).add_to(initialize_map)
initialize_map

Wychwood (94)
Yonge-Eglinton (100)
Yonge-St.Clair (97)
York University Heights (27)
Yorkdale-Glen Park (31)
Lambton Baby Point (114)
Lansing-Westgate (38)
Lawrence Park North (105)
Lawrence Park South (103)
Leaside-Bennington (56)
Little Portugal (84)
Long Branch (19)
Malvern (132)
Maple Leaf (29)
Markland Wood (12)
Milliken (130)
Mimico (includes Humber Bay Shores) (17)
Morningside (135)
Moss Park (73)
Mount Dennis (115)
Mount Olive-Silverstone-Jamestown (2)
Mount Pleasant East (99)
Mount Pleasant West (104)
New Toronto (18)
Newtonbrook East (50)
Newtonbrook West (36)
Niagara (82)
North Riverdale (68)
North St.James Town (74)
O'Connor-Parkview (54)
Oakridge (121)
Oakwood Village (107)
Old East York (58)
Palmerston-Little Italy (80)
Parkwoods-Donalda (45)
Pelmo Park-Humberlea (23)
Playter Estates-Danforth (67)
Pleasant View (46)
Princess-Rosethorn (10)
Regent Park (72)
Rexdale-Kipling (4)
Rockcliffe-Smythe (111)
Roncesvalles (86)
Rosedale-Moore Park (98)
Rouge (131)
Runnymede-Bloor Wes

In [75]:
initialize_map.save('map1.html')

In [68]:
initialize_map

AssertionError: ignored